Link to Section 3: https://datahub.berkeley.edu/user/kc1558628/notebooks/Problem%20Set%201%20(KC%20Harris)/Problem%20Set%201%20Section%203%20(KC%20Harris).ipynb#

Link to Section 6: https://datahub.berkeley.edu/user/kc1558628/notebooks/Problem%20Set%201%20(KC%20Harris)/Problem%20Set%201%20Section%206%20(KC%20Harris).ipynb

In [112]:
# import libraries
!pip install folium --upgrade

from numpy.random import *
import pandas as pd
import numpy as np
from collections import Counter
import matplotlib.pyplot as plt
%matplotlib inline
import folium
import json
import os
from branca.colormap import linear
import branca.colormap

import folium.plugins # The Folium Javascript Map Library
from folium.plugins import HeatMap
from folium.plugins import HeatMapWithTime
from folium import Choropleth

In [3]:
#opening the data
# df = pd.read_csv('Police_Department_Incident_Reports__2018_to_Present (web).csv')
df_small = pd.read_csv('Sample_10k_Police_Department_Incident_Reports__2018_to_Present.csv')
df_small.shape
df_small.head()


# incident_data_np = Table().read_table('Sample_10k_Police_Department_Incident_Reports__2018_to_Present.csv')
# incident_data_np

FileNotFoundError: [Errno 2] No such file or directory: 'Sample_10k_Police_Department_Incident_Reports__2018_to_Present.csv'

# 4) Geographic Data

4.1) Plot individual incidents in 2019 as points on a map of San Francisco You’ll want to use folium (which you saw in lab) and geopandas, which extends DataFrames from pandas to GeoDataFrames, which include geographic information. Find the documentation on GeoDataFrames here: https://geopandas.org/en/stable/docs/reference/api/geopandas.GeoDataFrame.html#geopandas.GeoDataFrame

In [102]:
# GeoJSON file
sf_neighborhoods = os.path.join('C:\\Users\\kharr\\Documents\\GitHub\\Legal-Studies-123-Problem-Set-1\\Data\\SF Find Neighborhoods.geojson')
geo_json_data = json.load(open(sf_neighborhoods))


# Incident Report Data
sfpd_ir_2018_2022 = os.path.join('C:\\Users\\kharr\\Documents\\GitHub\\Legal-Studies-123-Problem-Set-1\\Data\\Sample_10k_Police_Department_Incident_Reports__2018_to_Present.csv')
ir = pd.read_csv(sfpd_ir_2018_2022)

In [60]:
ir_2019 = ir[ir['Incident Year'] == 2019]

In [57]:
print('variables: ', list(ir.columns))

ir_loc_nan_na = ir.dropna(subset = ['Latitude', 'Longitude'], inplace=True)

lat = ir['Latitude'].values 
lon = ir['Longitude'].values 

ir_locs = np.vstack((lat, lon)).transpose().tolist() 
ir_locs

gdf = geopandas.GeoDataFrame(d, crs="EPSG:4326")

variables:  ['Index', 'Incident Datetime', 'Incident Date', 'Incident Time', 'Incident Year', 'Incident Day of Week', 'Report Datetime', 'Row ID', 'Incident ID', 'Incident Number', 'CAD Number', 'Report Type Code', 'Report Type Description', 'Filed Online', 'Incident Code', 'Incident Category', 'Incident Subcategory', 'Incident Description', 'Resolution', 'Intersection', 'CNN', 'Police District', 'Analysis Neighborhood', 'Supervisor District', 'Latitude', 'Longitude', 'Point', 'Neighborhoods', 'ESNCAG - Boundary File', 'Central Market/Tenderloin Boundary Polygon - Updated', 'Civic Center Harm Reduction Project Boundary', 'HSOC Zones as of 2018-06-05', 'Invest In Neighborhoods (IIN) Areas', 'Current Supervisor Districts', 'Current Police Districts', 'Hour']


NameError: name 'geopandas' is not defined

In [55]:
heatmap = HeatMap(ir_locs, radius = 10) 

# Add it to your Berkeley map.
sf_map.add_child(heatmap)

4.1.1) Does crime seem randomly distributed in space, or do incidents tend to cluster close together?

I think this is a trick question. For most of the reports, it appears that the lat and long values are based on intersection locations, meaning they're clustered. 

4.1.2) Shade the points by type of crime and analyze whether certain neighborhoods experience certain types of crime more often.

4.1.3) Propose social scientific explanations for the patterns that you find.

4.2) Merge the incidents data with the GeoJSON file which contains the information on the boundaries of neighborhoods in San Francisco.

Hint: Merging the incidents data, which includes the location of each incident, with the SF neighborhoods data, which describes each SF neighborhood and the geographic region it occupies, can be thought of as a spatial join across the two tables. Look back at the GeoDataFrame documentation to perform this join. In the next problems, you will use this merged data to make visualizations of the frequency of various crimes by neighborhood. 

Important Note: When running the spatial join, you may get weird exceptions from inside of geopandas. This can happen when necessary libraries are not installed. To be sure you have what you need, run the following: https://www.notion.so/karatechop/Merge-Instructions-6a2faf34a0e1467ba3dfb2584101c7e9


If you spend 30 minutes or more on errors coming from importing geopandas, or other internal errors in geopandas, ask in office hours, in lab, or on Piazza. Hint: When making a GeoDataFrame, note that there is a crs attribute (the coordinate refer-
ence system) that you should take care to set to {’init’: ’epsg:4326’}. You can do this by either assigning to it directly (like mygeodataframe.crs = {’init’: ’epsg:4326’}) or by using the keyword argument to the constructor (GeoDataFrame(..., crs={’init’: ’epsg:4326’}). This short geopandas guide explains what this means and what the CRS is for: https://geopandas.org/en/stable/docs/user_guide/projections.html


# 5) Mapping Incidents

5.1) Construct a choropleth map, coloring in each neighborhood by how many incidents it had in 2019. Then, construct several maps that explore differences by day of week, time of year, time of day etc.

In [155]:
ir_2019['Analysis Neighborhood'].unique().size

41

In [143]:
ir_2019_grouped_neighborhood = ir_2019.groupby(['Analysis Neighborhood']).size().to_frame(name = 'Count').sort_values("Count", ascending = False).reset_index()
ir_2019_grouped_neighborhood

Analysis Neighborhood  Count
0                          Mission    283
1                       Tenderloin    262
2                  South of Market    234
3   Financial District/South Beach    215
4            Bayview Hunters Point    159
5                 Western Addition     81
6              Castro/Upper Market     80
7                     Russian Hill     69
8                      North Beach     67
9                           Marina     66
10                    Hayes Valley     64
11                 Sunset/Parkside     63
12                        Nob Hill     59
13                  Outer Richmond     55
14                       Chinatown     51
15                       Excelsior     50
16                  Bernal Heights     48
17              West of Twin Peaks     47
18                    Inner Sunset     45
19                 Pacific Heights     44
20                  Inner Richmond     41
21                       Japantown     40
22                    Potrero Hill     40
23                       Lakeshore     38
24                     Mission Bay     38
25      Oceanview/Merced/Ingleside     36
26                  Haight Ashbury     35
27                   Outer Mission     33
28               Visitacion Valley     33
29                Golden Gate Park     30
30                         Portola     26
31                Presidio Heights     20
32               Lone Mountain/USF     20
33                       Glen Park     17
34                      Noe Valley     13
35                 Treasure Island      9
36                        Presidio      8
37                      Twin Peaks      7
38                    McLaren Park      2
39                    Lincoln Park      2
40                        Seacliff      1

In [144]:
colormap = linear.BuGn_03.scale(
    ir_2019_grouped_neighborhood.Count.min(),
    ir_2019_grouped_neighborhood.Count.max())

colormap

In [145]:
ir_2019_grouped_neighborhood_dict = ir_2019_grouped_neighborhood.set_index('Analysis Neighborhood')['Count']
ir_2019_grouped_neighborhood_dict

Analysis Neighborhood
Mission                           283
Tenderloin                        262
South of Market                   234
Financial District/South Beach    215
Bayview Hunters Point             159
Western Addition                   81
Castro/Upper Market                80
Russian Hill                       69
North Beach                        67
Marina                             66
Hayes Valley                       64
Sunset/Parkside                    63
Nob Hill                           59
Outer Richmond                     55
Chinatown                          51
Excelsior                          50
Bernal Heights                     48
West of Twin Peaks                 47
Inner Sunset                       45
Pacific Heights                    44
Inner Richmond                     41
Japantown                          40
Potrero Hill                       40
Lakeshore                          38
Mission Bay                        38
Oceanview/Merced/Ingleside  

In [146]:
geo_json_data

{'type': 'FeatureCollection',
 'features': [{'type': 'Feature',
   'properties': {'link': 'http://en.wikipedia.org/wiki/Sea_Cliff,_San_Francisco,_California',
    'name': 'Seacliff'},
   'geometry': {'type': 'MultiPolygon',
    'coordinates': [[[[-122.49345526799993, 37.78351817100008],
       [-122.49372649999992, 37.78724665100009],
       [-122.49358666699993, 37.78731259500006],
       [-122.49360569399994, 37.78752774600008],
       [-122.49283007399993, 37.787882585000034],
       [-122.4927566799999, 37.78773917700005],
       [-122.48982906399993, 37.789482184000065],
       [-122.48899105699991, 37.78928318700008],
       [-122.4878640209999, 37.78958817900008],
       [-122.48736904899994, 37.78942984100007],
       [-122.48598032899991, 37.79080370600008],
       [-122.48581537399991, 37.79070384600004],
       [-122.48557750799989, 37.790559847000054],
       [-122.4850531269999, 37.79036813300007],
       [-122.4842660519999, 37.789411709000035],
       [-122.4840770679999

In [147]:
sf_map = folium.Map(sf_coords, zoom_start = 12.5)

folium.GeoJson(
    geo_json_data,
    name='crime by neighborhood',
    style_function=lambda feature: {
        'fillColor': colormap(ir_2019_grouped_neighborhood_dict[Feature['name']]),
        'color': 'black',
        'weight': 1,
        'dashArray': '5, 5',
        'fillOpacity': 0.9,
    }
).add_to(sf_map)

folium.LayerControl().add_to(sf_map)

sf_map

NameError: name 'Feature' is not defined

In [148]:
sf_coords = (37.76, -122.45)
sf_map = folium.Map(sf_coords, zoom_start = 12.5)


folium.Choropleth(
    geo_data = geo_json_data,
    name = 'crime by neighborhood',
    data = ir_2019_grouped_neighborhood,
    columns=['Analysis Neighborhood', 'Count'],
    key_on='properties.name',
    fill_color='YlGn',
    legend_name=f'Crime by District in SF',
).add_to(sf_map)
    
sf_map
    

5.2) Do you notice any patterns? Are there particular neighborhoods where crime concentrates more heavily?

5.3) Construct a heat map of crime. How does the heat map compare to the choropleth map? Are neighborhoods a reasonably good
proxy for the actual concentration of crime?